In [7]:
from openai import OpenAI
import openai
import os
import backoff

api_key = os.getenv("YEScale_OpenAI")
# gpt-4.1-mini-2025-04-14
# gpt-4.1-2025-04-14
model_name = "gpt-4.1-2025-04-14"
embedder_name = "text-embedding-3-small"
client = OpenAI(
    api_key=api_key,
    base_url="https://api.yescale.io/v1"
    )

# Backoff for API calling (in case of rate limit, error, etc.)
@backoff.on_exception(backoff.expo, openai.RateLimitError, max_time=999, max_tries=99)
def completions_with_backoff(**kwargs):
    return client.chat.completions.create(**kwargs)

def ask_gpt(sys: str, user: str, max_token=500) -> str:
    response = completions_with_backoff(
        model=model_name,
        messages=[
            {"role": "system", "content": sys},
            {"role": "user", "content": user},
        ],
        max_tokens=max_token,
        n=1,
        stop=None,
        temperature=0.3,
    )
    return response.choices[0].message.content

def get_embedding(text):
    response = client.embeddings.create(
        input=text,
        model=embedder_name
    )
    return response.data[0].embedding

In [8]:
import pandas as pd

df = pd.read_csv('Dataset/ViMedical_Disease/ViMedical_Disease.csv', encoding='utf-8')
print(df.head())

     Disease                                           Question
0  Alzheimer  Tôi hiện đang có các triệu chứng như hay quên ...
1  Alzheimer  Tôi đang cảm thấy khó khăn khi tham gia cuộc h...
2  Alzheimer  Tôi hay quên nghĩa của từ và không thể theo dõ...
3  Alzheimer  Tôi hiện đang có các triệu chứng như thay đổi ...
4  Alzheimer  Tôi đang cảm thấy chán nản và muốn từ bỏ các s...


In [ ]:
from tqdm import tqdm

disease = df['Disease'].unique()
heart_disease = []
respiretory_disease = []
for dis in tqdm(disease, desc="Processing diseases", unit="disease"):
    while True:
        res = ask_gpt("Hãy xác định xem bệnh này là bệnh tim mạch hay bệnh hô hấp. Nếu là bệnh tim mạch, trả lời '1', hô hấp '2', không phải cả hai thì là '0'. Không cần giải thích gì thêm.", dis, 1)
        if res in ['0', '1', '2']:
            if res == '1':
                heart_disease.append(dis)
            elif res == '2':
                respiretory_disease.append(dis)
            break
with open("Dataset/ViMedical_Disease/heart_disease.txt", "w", encoding="utf-8") as file:
    for item in heart_disease:
        file.write(item + "\n")
with open("Dataset/ViMedical_Disease/respiretory_disease.txt", "w", encoding="utf-8") as file:
    for item in respiretory_disease:
        file.write(item + "\n")

Processing diseases: 100%|██████████| 603/603 [14:20<00:00,  1.43s/disease]
